Lambda School Data Science

*Unit 4, Sprint 1, Module 3*

---

# Document Classification (Prepare)

Today's guided module project will be different. You already know how to do classification. You ready know how to extract features from documents. So? That means you're ready to combine and practice those skills in a kaggle competition. We we will open with a five minute sprint explaining the competition, and then give you 25 minutes to work. After those twenty five minutes are up, I will give a 5-minute demo an NLP technique that will help you with document classification (*and **maybe** the competition*).

Today's all about having fun and practicing your skills. The competition will begin

## Learning Objectives
* <a href="#p1">Part 1</a>: Text Feature Extraction & Classification Pipelines
* <a href="#p2">Part 2</a>: Latent Semantic Indexing
* <a href="#p3">Part 3</a>: Word Embeddings with Spacy

# Text Feature Extraction & Classification Pipelines (Learn)
<a id="p1"></a>

## Overview

Sklearn pipelines allow you to stitch together multiple components of a machine learning process. The idea is that you can pass you raw data and get predictions out of the pipeline. This ability to pass raw input and receive a prediction from a singular class makes pipelines well suited for production, because you can pickle a a pipeline without worry about other data preprocessing steps. 

*Note:* Each time we call the pipeline during grid search, each component is fit again. The vectorizer (tf-idf) is transforming our entire vocabulary during each cross-validation fold. That transformation adds significant run time to our grid search. There *might* be interactions between the vectorizer and our classifier, so we estimate their performance together in the code below. However, if your goal is to reduce run time. Train your vectorizer separately (ie out of the grid-searched pipeline). 

In [1]:
# Import Statements
from sklearn.pipeline import Pipeline
from sklearn.datasets import fetch_20newsgroups
from sklearn.ensemble import RandomForestClassifier
from sklearn.model_selection import GridSearchCV
from sklearn.feature_extraction.text import TfidfVectorizer

In [2]:
# Dataset

from sklearn.datasets import fetch_20newsgroups

# Try changing to politics and space, for clearer distinctions
categories = ['alt.atheism',
              'talk.religion.misc']

data = fetch_20newsgroups(subset='train', categories=categories)

In [4]:
# Print out data sample

# Sklearn data, not a dataframe, looks like dictionary
#data

# See dictionary keys
#data.keys()

# Just need the data
#data['data']

# Length of the data, how many posts, 857
len(data['data'])

# The target, array
#data['target']

# Shape of target data, array is size 857
#data['target'].shape

# Show one post
#data['data'][2]

857

In [5]:
# Create Pipeline Components
# Great to keep code clean, and serialize to use later, while also allowing hyperparamter search across the whole pipeline, at the same time

vect = TfidfVectorizer(stop_words='english', ngram_range=(1,2))
rfc = RandomForestClassifier()

In [7]:
# Define the Pipeline
pipe = Pipeline([
                 #Vectorizer
                 ('vect', vect),
                 # Classifier
                 ('clf', rfc)
                ])

# The pipeline puts together a bunch fit then transform,fit then predict. 

In [8]:
# Consider limiting tokens to lower number, of higher tfidf score

parameters = {
    'vect__max_df': ( 0.75, 1.0),
    'vect__min_df': (.02, .05),
    'vect__max_features': (500,1000),
    'clf__n_estimators':(5, 10,),
    'clf__max_depth':(15,20)
}

grid_search = GridSearchCV(pipe,parameters, cv=5, n_jobs=-1, verbose=1)
grid_search.fit(data.data, data.target)

Fitting 5 folds for each of 32 candidates, totalling 160 fits


[Parallel(n_jobs=-1)]: Using backend LokyBackend with 4 concurrent workers.
[Parallel(n_jobs=-1)]: Done  42 tasks      | elapsed:   15.8s
[Parallel(n_jobs=-1)]: Done 160 out of 160 | elapsed:   51.2s finished


GridSearchCV(cv=5, error_score=nan,
             estimator=Pipeline(memory=None,
                                steps=[('vect',
                                        TfidfVectorizer(analyzer='word',
                                                        binary=False,
                                                        decode_error='strict',
                                                        dtype=<class 'numpy.float64'>,
                                                        encoding='utf-8',
                                                        input='content',
                                                        lowercase=True,
                                                        max_df=1.0,
                                                        max_features=None,
                                                        min_df=1,
                                                        ngram_range=(1, 2),
                                                        no

In [9]:
grid_search.best_score_

0.8786481708146334

In [16]:
# Best params is actually best hyperparameters

grid_search.best_params_

{'clf__max_depth': 15,
 'clf__n_estimators': 10,
 'vect__max_df': 1.0,
 'vect__max_features': 1000,
 'vect__min_df': 0.02}

In [15]:
grid_search.best_estimator_

Pipeline(memory=None,
         steps=[('vect',
                 TfidfVectorizer(analyzer='word', binary=False,
                                 decode_error='strict',
                                 dtype=<class 'numpy.float64'>,
                                 encoding='utf-8', input='content',
                                 lowercase=True, max_df=1.0, max_features=1000,
                                 min_df=0.02, ngram_range=(1, 2), norm='l2',
                                 preprocessor=None, smooth_idf=True,
                                 stop_words='english', strip_accents=None,
                                 sublinear_tf=False,
                                 token_pa...
                 RandomForestClassifier(bootstrap=True, ccp_alpha=0.0,
                                        class_weight=None, criterion='gini',
                                        max_depth=15, max_features='auto',
                                        max_leaf_nodes=None, max_samples=None,


In [10]:
grid_search.predict(['Send me lots of money now', 'you won the lottery in Nigeria'])

array([1, 1])

In [20]:
grid_search.predict(['God is alive and well', "Some people don't believe in God","Is Data Science a religion?"])

array([1, 1, 1])

In [17]:
grid_search.predict_proba(['Send me lots of money now', 'you won the lottery in Nigeria'])

array([[0.40325652, 0.59674348],
       [0.40325652, 0.59674348]])

## Follow Along 

What you should be doing now:
1. Join the Kaggle Competition
2. Download the data
3. Train a model (try using the pipe method I just demoed)

## Challenge

You're trying to achieve 75% Accuracy on your model.

## Latent Semantic Indexing (Learn)
<a id="p2"></a>

## Overview

In [11]:
# Import

from sklearn.decomposition import TruncatedSVD

svd = TruncatedSVD(n_components=100, # Just here for demo. 
                   algorithm='randomized',
                   n_iter=10)

In [12]:
params = { 
    'lsi__svd__n_components': [10,100,250],
    'lsi__vect__max_df':[.9, .95, 1.0],
    'clf__n_estimators':[5,10,20]
}

In [13]:
# LSI
lsi = Pipeline([('vect', vect), ('svd', svd)])


# Pipe
pipe = Pipeline([('lsi', lsi), ('clf', rfc)])

In [14]:
print(pipe)

Pipeline(memory=None,
         steps=[('lsi',
                 Pipeline(memory=None,
                          steps=[('vect',
                                  TfidfVectorizer(analyzer='word', binary=False,
                                                  decode_error='strict',
                                                  dtype=<class 'numpy.float64'>,
                                                  encoding='utf-8',
                                                  input='content',
                                                  lowercase=True, max_df=1.0,
                                                  max_features=None, min_df=1,
                                                  ngram_range=(1, 2), norm='l2',
                                                  preprocessor=None,
                                                  smooth_idf=True,
                                                  stop_words='english',
                                                  strip_a

In [21]:
# Fit
grid_search = GridSearchCV(pipe,params, cv=5, n_jobs=-1, verbose=1)
grid_search.fit(data.data, data.target)

Fitting 5 folds for each of 27 candidates, totalling 135 fits


[Parallel(n_jobs=-1)]: Using backend LokyBackend with 4 concurrent workers.
[Parallel(n_jobs=-1)]: Done  42 tasks      | elapsed:  6.9min
[Parallel(n_jobs=-1)]: Done 135 out of 135 | elapsed: 23.2min finished


GridSearchCV(cv=5, error_score=nan,
             estimator=Pipeline(memory=None,
                                steps=[('lsi',
                                        Pipeline(memory=None,
                                                 steps=[('vect',
                                                         TfidfVectorizer(analyzer='word',
                                                                         binary=False,
                                                                         decode_error='strict',
                                                                         dtype=<class 'numpy.float64'>,
                                                                         encoding='utf-8',
                                                                         input='content',
                                                                         lowercase=True,
                                                                         max_df=1.0,
             

In [22]:
grid_search.best_score_

0.9066639466884265

In [23]:
best_pipeline = grid_search.best_estimator_

In [29]:
pipe.named_steps['lsi']

Pipeline(memory=None,
         steps=[('vect',
                 TfidfVectorizer(analyzer='word', binary=False,
                                 decode_error='strict',
                                 dtype=<class 'numpy.float64'>,
                                 encoding='utf-8', input='content',
                                 lowercase=True, max_df=1.0, max_features=None,
                                 min_df=1, ngram_range=(1, 2), norm='l2',
                                 preprocessor=None, smooth_idf=True,
                                 stop_words='english', strip_accents=None,
                                 sublinear_tf=False,
                                 token_pattern='(?u)\\b\\w\\w+\\b',
                                 tokenizer=None, use_idf=True,
                                 vocabulary=None)),
                ('svd',
                 TruncatedSVD(algorithm='randomized', n_components=100,
                              n_iter=10, random_state=None, tol=0.0))],

In [30]:
pipe.named_steps['lsi'].named_steps['vect']

TfidfVectorizer(analyzer='word', binary=False, decode_error='strict',
                dtype=<class 'numpy.float64'>, encoding='utf-8',
                input='content', lowercase=True, max_df=1.0, max_features=None,
                min_df=1, ngram_range=(1, 2), norm='l2', preprocessor=None,
                smooth_idf=True, stop_words='english', strip_accents=None,
                sublinear_tf=False, token_pattern='(?u)\\b\\w\\w+\\b',
                tokenizer=None, use_idf=True, vocabulary=None)

In [38]:
data['data'][0]
#data['data'][1]

'From: mangoe@cs.umd.edu (Charley Wingate)\nSubject: Benediktine Metaphysics\nLines: 24\n\nBenedikt Rosenau writes, with great authority:\n\n>     IF IT IS CONTRADICTORY IT CANNOT EXIST.\n\n"Contradictory" is a property of language.  If I correct this to\n\n\n      THINGS DEFINED BY CONTRADICTORY LANGUAGE DO NOT EXIST\n\nI will object to definitions as reality.  If you then amend it to\n\n      THINGS DESCRIBED BY CONTRADICTORY LANGUAGE DO NOT EXIST\n\nthen we\'ve come to something which is plainly false.  Failures in\ndescription are merely failures in description.\n\n(I\'m not an objectivist, remember.)\n\n\n-- \nC. Wingate        + "The peace of God, it is no peace,\n                  +    but strife closed in the sod.\nmangoe@cs.umd.edu +  Yet, brothers, pray for but one thing:\ntove!mangoe       +    the marv\'lous peace of God."\n'

In [32]:
# Vectorizer can be passed transform to transform data, ie. one test instance

# Sparse Matrix

best_pipeline.named_steps['lsi'].named_steps['vect'].transform([data['data'][0]])

<1x111645 sparse matrix of type '<class 'numpy.float64'>'
	with 105 stored elements in Compressed Sparse Row format>

In [35]:
# To dense

best_pipeline.named_steps['lsi'].named_steps['vect'].transform([data['data'][0]]).todense()

# Incredibly sparse matrix, looking at how many elements are 0 in this matrix, and the shape below. 
# Every document doesn't include all of the words, only a small subset, which is problematic.

matrix([[0., 0., 0., ..., 0., 0., 0.]])

In [37]:
# Shape

best_pipeline.named_steps['lsi'].named_steps['vect'].transform([data['data'][0]]).todense().shape

# High demensionality vector, lots of tokens!

(1, 111645)

In [40]:
# By removing the vectorization, and todense, the pipeline returns a much smaller vector

best_pipeline.named_steps['lsi'].transform([data['data'][0]])

array([[ 0.08469022,  0.03195783, -0.11512258, -0.05182049,  0.02827522,
        -0.03654368, -0.03993008, -0.02670944,  0.15820419, -0.12917498,
         0.40248897, -0.20935217,  0.00446447,  0.24959841, -0.18826176,
         0.03834018,  0.05833439, -0.0271165 ,  0.10774228, -0.00419744,
        -0.0345188 , -0.04729655,  0.03815917, -0.01395501,  0.01455444,
        -0.02227574,  0.06702441, -0.01436793,  0.07250481, -0.02664355,
        -0.03072251,  0.02084113, -0.03344635,  0.01731784, -0.00356324,
        -0.01630569,  0.01604913,  0.05383652,  0.01627444,  0.04061352,
         0.01397297,  0.0178885 , -0.00489106,  0.00615848, -0.01715768,
         0.09053478,  0.026012  , -0.00733315, -0.04274561,  0.06385591,
         0.04583523, -0.05827524,  0.00323977, -0.00238198, -0.00264061,
         0.02894414,  0.0535675 , -0.0160409 , -0.04955994, -0.06751431,
         0.05101868,  0.01691263, -0.07842701, -0.0058383 ,  0.03318619,
        -0.03441228,  0.00202741,  0.00771784, -0.0

In [42]:
# Shape

best_pipeline.named_steps['lsi'].transform([data['data'][0]]).shape

(1, 100)

In [43]:
# Notice how the number of svd components matches the number dimensionality of the best_pipeline results array

grid_search.best_params_

{'clf__n_estimators': 20,
 'lsi__svd__n_components': 100,
 'lsi__vect__max_df': 0.95}

## Follow Along
1. Join the Kaggle Competition
2. Download the data
3. Train a model & try: 
    - Creating a Text Extraction & Classification Pipeline
    - Tune the pipeline with a `GridSearchCV` or `RandomizedSearchCV`
    - Add some Latent Semantic Indexing (lsi) into your pipeline. *Note:* You can grid search a nested pipeline, but you have to use double underscores ie `lsi__svd__n_components`
4. Make a submission to Kaggle 


## Challenge

Continue to apply Latent Semantic Indexing (LSI) to various datasets. 

# Word Embeddings with Spacy (Learn)
<a id="p3"></a>

# Overview

In [44]:
import spacy
nlp = spacy.load("en_core_web_lg")

In [45]:
doc = nlp("Two bananas in pyjamas")

In [46]:
bananas_vector = doc.vector
print(len(bananas_vector))

300


In [47]:
def get_word_vectors(docs):
    return [nlp(doc).vector for doc in docs]

In [48]:
# Use just this function to turn raw data into vector form

%%time
X = get_word_vectors(data.data)

len(X) == len(data.data)

CPU times: user 2min 35s, sys: 6.12 s, total: 2min 41s
Wall time: 4min 27s


True

In [49]:
# Turn text data into values directly, without tfidf vectorizer and single value decomposition, or latent semantic indexing. Data to vectors.
X

[array([-2.24261973e-02,  1.16948791e-01, -1.40623569e-01, -8.97146240e-02,
         5.67572452e-02,  2.33658105e-02, -1.04296878e-02, -3.83221991e-02,
        -3.14497203e-02,  1.60095787e+00, -1.52854711e-01,  7.60015845e-02,
         3.35256122e-02, -3.82818922e-04, -8.83924514e-02, -2.05108356e-02,
        -6.14920035e-02,  8.94030511e-01, -1.21286541e-01, -1.76449474e-02,
         3.00883572e-03, -2.65389066e-02,  5.69479540e-03,  3.20637971e-02,
         1.32068964e-02,  3.05791143e-02, -4.84521687e-02, -4.10817144e-03,
         3.47910374e-02, -2.70029213e-02, -4.06233370e-02,  9.24473107e-02,
        -4.75446433e-02,  1.73872765e-02,  7.95437545e-02, -3.22926454e-02,
         2.25547757e-02,  3.64724770e-02, -8.19447264e-02, -1.99605860e-02,
        -1.32072708e-02,  3.00613586e-02,  1.62900332e-02, -1.20532522e-02,
        -8.38013925e-03, -7.63823558e-03, -6.95322007e-02,  3.03549431e-02,
        -2.01541363e-04,  1.80957410e-02, -4.44174521e-02,  8.56731161e-02,
        -6.4

In [52]:
# How many documents?

len(X)

857

In [50]:
# Every document is a vector of this shape dimensionality

X[0].shape

(300,)

In [53]:
# Fit the random forest classifier, not using pipelines right here, just the model directly

rfc.fit(X, data['target'])

RandomForestClassifier(bootstrap=True, ccp_alpha=0.0, class_weight=None,
                       criterion='gini', max_depth=None, max_features='auto',
                       max_leaf_nodes=None, max_samples=None,
                       min_impurity_decrease=0.0, min_impurity_split=None,
                       min_samples_leaf=1, min_samples_split=2,
                       min_weight_fraction_leaf=0.0, n_estimators=100,
                       n_jobs=None, oob_score=False, random_state=None,
                       verbose=0, warm_start=False)

In [54]:
# This is not a fair score, and the model should be run on the testing data for a more realistic score

rfc.score(X, data['target'])

1.0

In [69]:
train = fetch_20newsgroups(subset='train', categories=categories)

In [70]:
rfc.score(X, train['target'])

1.0

In [57]:
test = fetch_20newsgroups(subset='test', categories=categories)

In [72]:
#rfc.score(X, test['target'])

In [74]:
#X_test = get_word_vectors(test['description'])

In [75]:
#rfc.fit(X, train['ratingCategory'])

In [ ]:
#rfc.score(X, train['ratingCategory'])

In [ ]:
#rfc.predict(X_test)

In [ ]:
#test['ratingCategory'] = rfc.predict(X_test)

In [ ]:
#test[['id', 'ratingCategory']].to_csv('testSolutionSubmission.csv', header=True, index=False)

In [76]:
# To speed up processing

from multiprocessing import Pool, cpu_count

In [77]:
# Check how many cores in CPU

cpu_count()

4

In [1]:
# Pool is a utility function, so create a pool of workers, pass Pool an integer number, to use that many cores of CPU
# use Pool(cpu_count()) to change depending on which computer is being used

pool = Pool(2)

In [ ]:
# Create a function to return a single document

def to_vec(doc):
    return nlp(doc).vector

In [ ]:
# Map the function, to vectorize all the documents

#%%time
X = pool.map(to_vec, data['data'])

# Traceback means something went wrong

# Also, pools needs to be used with a context manager, ie. open pool, do some computations, and then close it.

# Try this: https://stackoverflow.com/questions/55035333/use-python-pool-with-context-manager-or-close-and-join

#with Pool() as p:
#    p.map_async(do_something, range(100))
#    # Do something else while tasks are running
#    p.join()

# Instead of do_something, function that takes one document and returns it as a vector
# Instead of range, replace with text data

# Context manager will do all of the computations

# pool.close() if stuck, however the context manager should pool and close for you

## Follow Along

## Challenge

What you should be doing now:
1. Join the Kaggle Competition
2. Download the data
3. Train a model & try: 
    - Creating a Text Extraction & Classification Pipeline
    - Tune the pipeline with a `GridSearchCV` or `RandomizedSearchCV`
    - Add some Latent Semantic Indexing (lsi) into your pipeline. *Note:* You can grid search a nested pipeline, but you have to use double underscores ie `lsi__svd__n_components`
    - Try to extract word embeddings with Spacy and use those embeddings as your features for a classification model.
4. Make a submission to Kaggle 

# Review

To review this module: 
* Continue working on the Kaggle competition
* Find another text classification task to work on